In [1]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

/kaggle/input/workshops/District to SSO master.csv
/kaggle/input/workshops/WS location details.csv
/kaggle/input/workshops/all_region_workshops.csv
/kaggle/input/mayforheatmap/May.parquet


In [2]:
!pip install fastparquet

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.7/1.7 MB 33.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 53.6 MB/s eta 0:00:00


In [3]:
df_tele = pd.read_parquet("/kaggle/input/mayforheatmap/May.parquet",engine='fastparquet')

In [4]:
df_tele.head()

vehicleId geohash_7 geohash_5   Latitude  Longitude  month  \
0  MAT790005L1J03687   tu7p9m8     tu7p9  25.255508  83.024368      5   
1  MAT797031L2K05106   tg22ctf     tg22c  18.445358  79.170914      5   
2  MAT790207NAJ09776   tukn0s1     tukn0  24.983597  84.399033      5   
3  MAT812033N5B03743   ttp45w5     ttp45  28.510208  77.502365      5   
4  MAT563010N5N13935   ttr8nsh     ttr8n  29.553909  78.338699      5   

          LOB                 PL             PPL region          state  \
0  MCV Trucks           LPT 1918      MCV LPT 19  North        Haryana   
1   HCV Const  SIGNA 2821.K. FBV  MAV Tippers 28  South      Telangana   
2  MCV Trucks         LPT1918 5L      MCV LPT 19  North        Haryana   
3  ICV Trucks          1109g LPT   ICV 10T - 12T  North  Uttar Pradesh   
4  ICV Trucks           1512 LPT   ICV 15T - 16T  North  Uttar Pradesh   

        city  rashturning  overspeeding  harshacceleration  harshbrake  \
0    GURGAON            1             0                  0           0   
1  HYDERABAD            1             0                  0           0   
2    GURGAON            1             0                  0           0   
3      NOIDA            1             0                  0           0   
4   BAREILLY            1             0                  0           0   

   VinCount         event_type  totalVinCount eventdate_1  
0         1  rashturning_event           1097  2024-05-01  
1         1  rashturning_event             95  2024-05-01  
2         1  rashturning_event            740  2024-05-01  
3         1  rashturning_event            357  2024-05-01  
4         1  rashturning_event            381  2024-05-01

In [5]:
grouped_df = df_tele.groupby(['geohash_7', 'geohash_5', 'Latitude', 'Longitude', 'month', 'LOB', 'PL', 'PPL']).size().reset_index(name='vehicleId_count')

In [6]:
grouped_df.shape

(5017561, 9)

In [7]:
df_tel = grouped_df.query("vehicleId_count >=8")

In [8]:
df_tel.shape

(55954, 9)

In [9]:
df_tel.head()

geohash_7 geohash_5  Latitude  Longitude  month         LOB       PL  \
61    t9qxz9r     t9qxz  8.401108  76.980515      5         LCV  610 SFC   
242   t9qygyn     t9qyg  8.251419  77.165909      5  ICV Trucks  912 LPK   
243   t9qygyq     t9qyg  8.252792  77.165909      5  ICV Trucks  912 LPK   
480   t9qyuc7     t9qyu  8.225327  77.205734      5         LCV   610 SK   
543   t9qyuq1     t9qyu  8.251419  77.181015      5         LCV   610 SK   

             PPL  vehicleId_count  
61        LCV 6T                8  
242   ICV Tipper               37  
243   ICV Tipper                9  
480  LCV Tippers               10  
543  LCV Tippers                9

In [10]:
df_workshop=pd.read_csv("/kaggle/input/workshops/all_region_workshops.csv")

In [11]:
df_workshop.head()

Division  Lattitude  Longitude     SSO  \
0     100B520-Sv&Pa-Nagercoils-AfjTor   8.190837  77.419204   Salem   
1      1001650-Sv&Pa-Nagercoil-ABTInM   8.198264  77.431443   Salem   
2  2088645-Sv&Pa-Neyyattinkara-KdmMot   8.368100  77.082080  Cochin   
3       2089374-Sv&Pa-Vallioor-SavAut   8.370961  77.601832   Salem   
4     2088731-Sv&Pa-Trivandrum-VjyMtr   8.424550  76.962980  Cochin   

        State  
0  Tamil Nadu  
1  Tamil Nadu  
2      Kerala  
3  Tamil Nadu  
4      Kerala

In [12]:
df_workshop['Divison_name'] = df_workshop['Division'].apply(lambda y : y.split('-')[2])

In [13]:
df_workshop = df_workshop.dropna()

In [14]:
df_workshop.info()

<class 'pandas.core.frame.DataFrame'>
Index: 1586 entries, 0 to 1590
Data columns (total 6 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   Division      1586 non-null   object 
 1   Lattitude     1586 non-null   float64
 2   Longitude     1586 non-null   float64
 3   SSO           1586 non-null   object 
 4   State         1586 non-null   object 
 5   Divison_name  1586 non-null   object 
dtypes: float64(2), object(4)
memory usage: 86.7+ KB


In [15]:
# Define the refined latitude and longitude ranges for India
lat_min, lat_max = 8.0, 37.0
lon_min, lon_max = 68.0, 97.0

# Additional filtering for known edge cases
def is_within_india(lat, lon):
    return (lat_min <= lat <= lat_max) and (lon_min <= lon <= lon_max) and \
           not ((lat > 35 and lon > 74) or (lat > 29 and lon > 82))

# Filter the DataFrame to keep only points within these ranges
df_workshop = df_workshop[df_workshop.apply(lambda x: is_within_india(x['Lattitude'], x['Longitude']), axis=1)]

In [16]:
import pandas as pd
import numpy as np
from sklearn.metrics import pairwise_distances

# Function to calculate haversine distance matrix in kilometers
def haversine_distance_matrix(workshops, telemetry):
    # Convert degrees to radians
    workshops_rad = np.radians(workshops)
    telemetry_rad = np.radians(telemetry)

    # Calculate the pairwise haversine distance matrix
    distances = pairwise_distances(telemetry_rad, workshops_rad, metric='haversine')
    # Convert radians to kilometers (earth radius ~6371 km)
    distances_km = distances * 6371
    return distances_km
'''

# Sample dataframes
# Workshop dataframe
workshops = pd.DataFrame({
    'lat': [12.9715987, 13.0826802, 12.2958104],
    'lon': [77.5945627, 80.2707184, 76.6393805]
})

# Telemetry dataframe
telemetry = pd.DataFrame({
    'lat': [12.9715987, 13.0826802, 11.0168445],
    'lon': [77.5945627, 80.2707184, 76.9558321]
})
'''
# Calculate the haversine distance matrix in kilometers
distances_km = haversine_distance_matrix(df_workshop[['Lattitude', 'Longitude']], df_tel[['Latitude', 'Longitude']])

# Function to classify points based on distance
def classify_points(workshops, telemetry, distances_km, threshold_km=15):
    min_distances = distances_km.min(axis=1)
    colors = ['green' if dist <= threshold_km else 'red' for dist in min_distances]
    result = telemetry.copy()
    result['distance'] = min_distances
    result['color'] = colors
    return result

# Classify the telemetry points
classified_points = classify_points(df_workshop, df_tel, distances_km)
#print(classified_points)


In [17]:
classified_points.head()

geohash_7 geohash_5  Latitude  Longitude  month         LOB       PL  \
61    t9qxz9r     t9qxz  8.401108  76.980515      5         LCV  610 SFC   
242   t9qygyn     t9qyg  8.251419  77.165909      5  ICV Trucks  912 LPK   
243   t9qygyq     t9qyg  8.252792  77.165909      5  ICV Trucks  912 LPK   
480   t9qyuc7     t9qyu  8.225327  77.205734      5         LCV   610 SK   
543   t9qyuq1     t9qyu  8.251419  77.181015      5         LCV   610 SK   

             PPL  vehicleId_count   distance  color  
61        LCV 6T                8   3.242639  green  
242   ICV Tipper               37  15.918548    red  
243   ICV Tipper                9  15.794365    red  
480  LCV Tippers               10  20.908218    red  
543  LCV Tippers                9  16.935987    red

In [18]:
classified_points.shape

(55954, 11)

In [19]:
# index

In [20]:
import pandas as pd
import numpy as np
from sklearn.metrics import pairwise_distances

# Function to calculate haversine distance matrix in kilometers
def haversine_distance_matrix(workshops, telemetry):
    # Convert degrees to radians
    workshops_rad = np.radians(workshops)
    telemetry_rad = np.radians(telemetry)

    # Calculate the pairwise haversine distance matrix
    distances = pairwise_distances(telemetry_rad, workshops_rad, metric='haversine')
    # Convert radians to kilometers (earth radius ~6371 km)
    distances_km = distances * 6371
    return distances_km

# Calculate the haversine distance matrix in kilometers
distances_km = haversine_distance_matrix(df_workshop[['Lattitude', 'Longitude']], classified_points[['Latitude', 'Longitude']])

# Find the minimum distance and corresponding workshop index for each telemetry point
min_distances = distances_km.min(axis=1)
min_indices = distances_km.argmin(axis=1)

# Add the workshop details to classified_points
classified_points['min_distance'] = min_distances
classified_points['workshop_index'] = min_indices
classified_points['workshop_name'] = classified_points['workshop_index'].apply(lambda x: df_workshop.iloc[x]['Divison_name'])
classified_points['workshop_lat'] = classified_points['workshop_index'].apply(lambda x: df_workshop.iloc[x]['Lattitude'])
classified_points['workshop_lon'] = classified_points['workshop_index'].apply(lambda x: df_workshop.iloc[x]['Longitude'])

# Drop the 'workshop_index' column if not needed
classified_points.drop(columns=['workshop_index'], inplace=True)

# Print the classified_points DataFrame with the added workshop details


In [21]:
classified_points

geohash_7 geohash_5   Latitude  Longitude  month         LOB  \
61        t9qxz9r     t9qxz   8.401108  76.980515      5         LCV   
242       t9qygyn     t9qyg   8.251419  77.165909      5  ICV Trucks   
243       t9qygyq     t9qyg   8.252792  77.165909      5  ICV Trucks   
480       t9qyuc7     t9qyu   8.225327  77.205734      5         LCV   
543       t9qyuq1     t9qyu   8.251419  77.181015      5         LCV   
...           ...       ...        ...        ...    ...         ...   
5016710   wjh0hx7     wjh0h  28.165512  95.827560      5   HCV Const   
5016729   wjh0jhc     wjh0j  28.151779  95.846786      5       Buses   
5017377   wjh5y2p     wjh5y  28.784866  95.909958      5  ICV Trucks   
5017458   wjhhkcq     wjhhk  28.879623  95.842667      5  MCV Trucks   
5017459   wjhhkcr     wjhhk  28.879623  95.844040      5  MCV Trucks   

                        PL             PPL  vehicleId_count    distance  \
61                 610 SFC          LCV 6T                8    3.242639   
242                912 LPK      ICV Tipper               37   15.918548   
243                912 LPK      ICV Tipper                9   15.794365   
480                 610 SK     LCV Tippers               10   20.908218   
543                 610 SK     LCV Tippers                9   16.935987   
...                    ...             ...              ...         ...   
5016710  SIGNA 2825.K. FBV  MAV Tippers 28               18   68.426582   
5016729        LPO10.2 FBV       ICV Buses               11   67.796458   
5017377            912 LPK      ICV Tipper                8  124.390992   
5017458  SIGNA 1923.K. FBV  MCV Tippers 19               18  124.805626   
5017459  SIGNA 1923.K. FBV  MCV Tippers 19               14  124.912872   

         color  min_distance  workshop_name  workshop_lat  workshop_lon  
61       green      3.242639     Trivandrum      8.424550     76.962980  
242        red     15.918548  Neyyattinkara      8.368100     77.082080  
243        red     15.794365  Neyyattinkara      8.368100     77.082080  
480        red     20.908218  Neyyattinkara      8.368100     77.082080  
543        red     16.935987  Neyyattinkara      8.368100     77.082080  
...        ...           ...            ...           ...           ...  
5016710    red     68.426582      Doomdooma     27.598651     95.556614  
5016729    red     67.796458      Doomdooma     27.598651     95.556614  
5017377    red    124.390992           Aalo     28.205521     94.821067  
5017458    red    124.805626           Aalo     28.205521     94.821067  
5017459    red    124.912872           Aalo     28.205521     94.821067  

[55954 rows x 15 columns]

In [22]:
classified_points.query("workshop_name=='Neyyattinkara'")

geohash_7 geohash_5  Latitude  Longitude  month         LOB  \
242    t9qygyn     t9qyg  8.251419  77.165909      5  ICV Trucks   
243    t9qygyq     t9qyg  8.252792  77.165909      5  ICV Trucks   
480    t9qyuc7     t9qyu  8.225327  77.205734      5         LCV   
543    t9qyuq1     t9qyu  8.251419  77.181015      5         LCV   
565    t9qyusg     t9qyu  8.244553  77.194748      5         LCV   
567    t9qyuss     t9qyu  8.243179  77.196121      5         LCV   
568    t9qyusu     t9qyu  8.244553  77.196121      5         LCV   
1313   t9qz5f0     t9qz5  8.273392  77.157669      5         LCV   
2368   t9qze26     t9qze  8.351669  77.138443      5      ScPass   
3291   t9qzm99     t9qzm  8.314590  77.235947      5         LCV   
3300   t9qzm9g     t9qzm  8.315964  77.238693      5         LCV   
4019   t9qzqh1     t9qzq  8.328323  77.257919      5     SCVPass   
4029   t9qzqhf     t9qzq  8.332443  77.259293      5     SCVPass   
4675   t9qzwhd     t9qzw  8.375015  77.259293      5         LCV   

                    PL          PPL  vehicleId_count   distance  color  \
242            912 LPK   ICV Tipper               37  15.918548    red   
243            912 LPK   ICV Tipper                9  15.794365    red   
480             610 SK  LCV Tippers               10  20.908218    red   
543             610 SK  LCV Tippers                9  16.935987    red   
565             610 SK  LCV Tippers                8  18.504406    red   
567             610 SK  LCV Tippers               22  18.718955    red   
568             610 SK  LCV Tippers               12  18.605943    red   
1313           710 SFC       LCV 7T               12  13.419008  green   
2368     Winger-School       Winger                8   6.464152  green   
3291            710 SK  LCV Tippers               11  17.943034    red   
3300            710 SK  LCV Tippers               10  18.179727    red   
4019  Magic EXPRESS M2     Magic M2               11  19.844049    red   
4029  Magic EXPRESS M2     Magic M2                9  19.894889    red   
4675            610 SK  LCV Tippers               11  19.509901    red   

      min_distance  workshop_name  workshop_lat  workshop_lon  
242      15.918548  Neyyattinkara        8.3681      77.08208  
243      15.794365  Neyyattinkara        8.3681      77.08208  
480      20.908218  Neyyattinkara        8.3681      77.08208  
543      16.935987  Neyyattinkara        8.3681      77.08208  
565      18.504406  Neyyattinkara        8.3681      77.08208  
567      18.718955  Neyyattinkara        8.3681      77.08208  
568      18.605943  Neyyattinkara        8.3681      77.08208  
1313     13.419008  Neyyattinkara        8.3681      77.08208  
2368      6.464152  Neyyattinkara        8.3681      77.08208  
3291     17.943034  Neyyattinkara        8.3681      77.08208  
3300     18.179727  Neyyattinkara        8.3681      77.08208  
4019     19.844049  Neyyattinkara        8.3681      77.08208  
4029     19.894889  Neyyattinkara        8.3681      77.08208  
4675     19.509901  Neyyattinkara        8.3681      77.08208

In [23]:
!pip install reverse_geocoder

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.2/2.2 MB 41.8 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... - \ done
  Created wheel for reverse_geocoder: filename=reverse_geocoder-1.5.1-py3-none-any.whl size=2268062 sha256=131cac2a49d38071eb7332a01de14977e2ffcaa6124df00bf504b29018bf7b46
  Stored in directory: /root/.cache/pip/wheels/bd/e5/88/eb139b6d6a26b8022d370ab991f7a836802fed9871975ec6d9
Successfully built reverse_geocoder


In [24]:
import pandas as pd
import reverse_geocoder as rg 
import pprint 

def reverseGeocode(coordinates): 
    result = rg.search(coordinates)
    return (result)



In [25]:
  if __name__=="__main__": 
    # Coordinates tuple.Can contain more than one pair.
    coordinates =list(zip(classified_points['Latitude'],classified_points['Longitude'])) # generates pair of (lat,long)
    data = reverseGeocode(coordinates)

    classified_points['name'] = [i['name'] for i in data]
    classified_points['admin1'] = [i['admin1'] for i in data]
    classified_points['admin2'] = [i['admin2'] for i in data]


Loading formatted geocoded file...


In [26]:
classified_points.head()

geohash_7 geohash_5  Latitude  Longitude  month         LOB       PL  \
61    t9qxz9r     t9qxz  8.401108  76.980515      5         LCV  610 SFC   
242   t9qygyn     t9qyg  8.251419  77.165909      5  ICV Trucks  912 LPK   
243   t9qygyq     t9qyg  8.252792  77.165909      5  ICV Trucks  912 LPK   
480   t9qyuc7     t9qyu  8.225327  77.205734      5         LCV   610 SK   
543   t9qyuq1     t9qyu  8.251419  77.181015      5         LCV   610 SK   

             PPL  vehicleId_count   distance  color  min_distance  \
61        LCV 6T                8   3.242639  green      3.242639   
242   ICV Tipper               37  15.918548    red     15.918548   
243   ICV Tipper                9  15.794365    red     15.794365   
480  LCV Tippers               10  20.908218    red     20.908218   
543  LCV Tippers                9  16.935987    red     16.935987   

     workshop_name  workshop_lat  workshop_lon         name      admin1  \
61      Trivandrum       8.42455      76.96298      Kovalam      Kerala   
242  Neyyattinkara       8.36810      77.08208  Kuzhithurai  Tamil Nadu   
243  Neyyattinkara       8.36810      77.08208  Kuzhithurai  Tamil Nadu   
480  Neyyattinkara       8.36810      77.08208     Colachel  Tamil Nadu   
543  Neyyattinkara       8.36810      77.08208  Kuzhithurai  Tamil Nadu   

            admin2  
61                  
242  Kanniyakumari  
243  Kanniyakumari  
480  Kanniyakumari  
543  Kanniyakumari

In [27]:
classified_points.rename(columns={'name':'City','admin1':'State','admin2':'District'},inplace=True)

In [28]:
classified_points

geohash_7 geohash_5   Latitude  Longitude  month         LOB  \
61        t9qxz9r     t9qxz   8.401108  76.980515      5         LCV   
242       t9qygyn     t9qyg   8.251419  77.165909      5  ICV Trucks   
243       t9qygyq     t9qyg   8.252792  77.165909      5  ICV Trucks   
480       t9qyuc7     t9qyu   8.225327  77.205734      5         LCV   
543       t9qyuq1     t9qyu   8.251419  77.181015      5         LCV   
...           ...       ...        ...        ...    ...         ...   
5016710   wjh0hx7     wjh0h  28.165512  95.827560      5   HCV Const   
5016729   wjh0jhc     wjh0j  28.151779  95.846786      5       Buses   
5017377   wjh5y2p     wjh5y  28.784866  95.909958      5  ICV Trucks   
5017458   wjhhkcq     wjhhk  28.879623  95.842667      5  MCV Trucks   
5017459   wjhhkcr     wjhhk  28.879623  95.844040      5  MCV Trucks   

                        PL             PPL  vehicleId_count    distance  \
61                 610 SFC          LCV 6T                8    3.242639   
242                912 LPK      ICV Tipper               37   15.918548   
243                912 LPK      ICV Tipper                9   15.794365   
480                 610 SK     LCV Tippers               10   20.908218   
543                 610 SK     LCV Tippers                9   16.935987   
...                    ...             ...              ...         ...   
5016710  SIGNA 2825.K. FBV  MAV Tippers 28               18   68.426582   
5016729        LPO10.2 FBV       ICV Buses               11   67.796458   
5017377            912 LPK      ICV Tipper                8  124.390992   
5017458  SIGNA 1923.K. FBV  MCV Tippers 19               18  124.805626   
5017459  SIGNA 1923.K. FBV  MCV Tippers 19               14  124.912872   

         color  min_distance  workshop_name  workshop_lat  workshop_lon  \
61       green      3.242639     Trivandrum      8.424550     76.962980   
242        red     15.918548  Neyyattinkara      8.368100     77.082080   
243        red     15.794365  Neyyattinkara      8.368100     77.082080   
480        red     20.908218  Neyyattinkara      8.368100     77.082080   
543        red     16.935987  Neyyattinkara      8.368100     77.082080   
...        ...           ...            ...           ...           ...   
5016710    red     68.426582      Doomdooma     27.598651     95.556614   
5016729    red     67.796458      Doomdooma     27.598651     95.556614   
5017377    red    124.390992           Aalo     28.205521     94.821067   
5017458    red    124.805626           Aalo     28.205521     94.821067   
5017459    red    124.912872           Aalo     28.205521     94.821067   

                City                    State        District  
61           Kovalam                   Kerala                  
242      Kuzhithurai               Tamil Nadu   Kanniyakumari  
243      Kuzhithurai               Tamil Nadu   Kanniyakumari  
480         Colachel               Tamil Nadu   Kanniyakumari  
543      Kuzhithurai               Tamil Nadu   Kanniyakumari  
...              ...                      ...             ...  
5016710         Tezu        Arunachal Pradesh  Lohit District  
5016729         Tezu        Arunachal Pradesh  Lohit District  
5017377        Motuo  Tibet Autonomous Region                  
5017458        Motuo  Tibet Autonomous Region                  
5017459        Motuo  Tibet Autonomous Region                  

[55954 rows x 18 columns]

In [29]:
classified_points.query("State =='Maharashtra'")

geohash_7 geohash_5   Latitude  Longitude  month        LOB  \
468213    tdu6unz     tdu6u  15.989914  73.662643      5        LCV   
472121    tdu9byw     tdu9b  15.812759  73.870010      5  HCV Const   
474094    tduetfz     tduet  16.099777  74.091110      5  HCV Const   
474110    tduew47     tduew  16.097031  74.096603      5  HCV Const   
474114    tduew4b     tduew  16.099777  74.092484      5  HCV Const   
...           ...       ...        ...        ...    ...        ...   
1621710   tgbcgfq     tgbcg  21.414413  79.978409      5  HCV Const   
1621723   tgbcgg9     tgbcg  21.421280  79.971542      5  HCV Cargo   
1622835   tgbfpsg     tgbfp  21.472092  80.139084      5  HCV Const   
1622955   tgbfrs6     tgbfr  21.513290  80.137711      5  HCV Const   
1636012   tgc4tgj     tgc4t  21.550369  80.416489      5        LCV   

                         PL                    PPL  vehicleId_count  \
468213            407g GOLD              LCV 4T PU                9   
472121    SIGNA 2823.K. FBV         MAV Tippers 28               15   
474094    SIGNA 2825.K. FBV         MAV Tippers 28               11   
474110    SIGNA 2825.K. FBV         MAV Tippers 28               12   
474114    SIGNA 2825.K. FBV         MAV Tippers 28               14   
...                     ...                    ...              ...   
1621710   SIGNA 2825.K. FBV         MAV Tippers 28                8   
1621723       LPS5525TC 4x2  Tractor Trailer 52/55               16   
1622835  SIGNA 2823.TK. FBV         MAV Tippers 28               11   
1622955  SIGNA 2823.TK. FBV         MAV Tippers 28               10   
1636012            407 GOLD              LCV 4T PU                8   

          distance  color  min_distance workshop_name  workshop_lat  \
468213   33.482437    red     33.482437     Kankavali     16.287694   
472121   30.780060    red     30.780060      Porvorim     15.538137   
474094   38.758226    red     38.758226    Gadhinglaj     16.234870   
474110   38.339520    red     38.339520    Gadhinglaj     16.234870   
474114   38.623109    red     38.623109    Gadhinglaj     16.234870   
...            ...    ...           ...           ...           ...   
1621710   1.967728  green      1.967728        Tirora     21.410000   
1621723   1.732336  green      1.732336        Tirora     21.410000   
1622835   8.704904  green      8.704904        Gondia     21.430000   
1622955  11.905287  green     11.905287        Gondia     21.430000   
1636012  25.210623    red     25.210623        Gondia     21.430000   

         workshop_lon        City        State    District  
468213      73.709160       Kudal  Maharashtra  Sindhudurg  
472121      73.833919  Savantvadi  Maharashtra  Sindhudurg  
474094      74.425660        Ajra  Maharashtra    Kolhapur  
474110      74.425660        Ajra  Maharashtra    Kolhapur  
474114      74.425660        Ajra  Maharashtra    Kolhapur  
...               ...         ...          ...         ...  
1621710     79.960000      Gondia  Maharashtra     Gondiya  
1621723     79.960000      Gondia  Maharashtra     Gondiya  
1622835     80.210000      Gondia  Maharashtra     Gondiya  
1622955     80.210000      Gondia  Maharashtra     Gondiya  
1636012     80.210000      Gondia  Maharashtra     Gondiya  

[7745 rows x 18 columns]

In [30]:
classified_points.to_csv("MayOutputCutOff_8.csv")

In [31]:
import plotly.graph_objects as go
import pandas as pd
import plotly.io as pio


# Filtering vehicles based on distance from the workshop
vehicles_near = classified_points[classified_points['distance'] < 10]
vehicles_far = classified_points[classified_points['distance'] >= 10]

# Define the figure
fig = go.Figure()

# Adding vehicle locations (distance < 15 kms) in green with transparency
fig.add_trace(go.Scattermapbox(
    lat=vehicles_near['Latitude'],
    lon=vehicles_near['Longitude'],
    mode='markers',
    marker=dict(color='green', size=15, opacity=0.5),
    name="Vehicles < 15Km"
))

# Adding vehicle locations (distance >= 15 kms) in red with transparency
fig.add_trace(go.Scattermapbox(
    lat=vehicles_far['Latitude'],
    lon=vehicles_far['Longitude'],
    mode='markers',
    marker=dict(color='red', size=15, opacity=0.5),
    name="Vehicles >= 15Km"
))

# Adding workshop locations in blue with transparency
fig.add_trace(go.Scattermapbox(
    lat=df_workshop['Lattitude'],
    lon=df_workshop['Longitude'],
    mode='markers',
    marker=dict(color='blue', size=15, opacity=0.5),
    name="Workshops"
))

# Update the layout of the plot to use a mapbox style and set the center and zoom level for India
fig.update_layout(
    mapbox_style='open-street-map', 
    mapbox_center_lon=78.9629,  # Approximate center longitude of India
    mapbox_center_lat=20.5937,  # Approximate center latitude of India
    mapbox_zoom=4,  # Zoom level for India
    legend=dict(yanchor="top", y=0.99, xanchor="left", x=0.01)
)

# Save the plot as an HTML file
pio.write_html(fig, file='map_plot.html', auto_open=True)

# Show the plot
#fig.show()


In [32]:
import plotly.graph_objects as go
import pandas as pd
import numpy as np


# Function to generate points of a circle
def generate_circle_points(lat, lon, radius_km, num_points=100):
    """
    Generate latitude and longitude points that form a circle around a central point.
    """
    R = 6371  # Radius of the Earth in km
    d = radius_km / R  # Angular distance in radians

    lat, lon = np.radians(lat), np.radians(lon)
    circle_lats, circle_lons = [], []
    for i in range(num_points):
        theta = 2 * np.pi * i / num_points
        lat_i = np.arcsin(np.sin(lat) * np.cos(d) + np.cos(lat) * np.sin(d) * np.cos(theta))
        lon_i = lon + np.arctan2(np.sin(theta) * np.sin(d) * np.cos(lat), np.cos(d) - np.sin(lat) * np.sin(lat_i))
        circle_lats.append(np.degrees(lat_i))
        circle_lons.append(np.degrees(lon_i))
    return circle_lats, circle_lons

# Generate circle points
center_lat, center_lon = 12.9715987, 77.5945627  # Center point (e.g., one of the workshops)
circle_radius_km = 10  # Radius of the circle in km
circle_lats, circle_lons = generate_circle_points(center_lat, center_lon, circle_radius_km)

# Define the figure
fig = go.Figure()

# Adding heatmap trace
fig.add_trace(go.Densitymapbox(
    lat=classified_points['Latitude'],
    lon=classified_points['Longitude'],
    radius=30,  # Adjust radius for kernel density estimation
    colorscale='YlOrRd',
    zmax=10,
    zmin=0,
    name='Density Heatmap'
))

# Adding vehicle locations (distance < 15 kms) in green with transparency
fig.add_trace(go.Scattermapbox(
    lat=classified_points['Latitude'],
    lon=classified_points['Longitude'],
    mode='markers',
    marker=dict(color='black', size=7, opacity=0.7),
    name="Vehicles"
))

# Adding workshop locations in blue with transparency
fig.add_trace(go.Scattermapbox(
    lat=df_workshop['Lattitude'],
    lon=df_workshop['Longitude'],
    mode='markers',
    marker=dict(color='blue', size=15, opacity=0.7),
    name="Workshops"
))

# Adding circle trace
fig.add_trace(go.Scattermapbox(
    lat=circle_lats,
    lon=circle_lons,
    mode='lines',
    line=dict(color='orange', width=2),
    name=f"Circle with {circle_radius_km}Km radius"
))

# Update the layout of the plot to use a mapbox style and set the center and zoom level for India
fig.update_layout(
    mapbox_style='open-street-map', 
    mapbox_center_lon=78.9629,  # Approximate center longitude of India
    mapbox_center_lat=20.5937,  # Approximate center latitude of India
    mapbox_zoom=5,  # Zoom level for India
    legend=dict(yanchor="top", y=0.99, xanchor="left", x=0.01)
)

# Save the plot as an HTML file
import plotly.io as pio
#pio.write_html(fig, file='map_plot.html', auto_open=True)

# Show the plot
#fig.show()


In [33]:
import plotly.graph_objects as go

# Filtering vehicles based on distance from the workshop
vehicles_near = classified_points[classified_points['distance'] < 15]
vehicles_far = classified_points[classified_points['distance'] >= 15]

# Define the figure
fig = go.Figure()

# Adding heatmap trace
fig.add_trace(go.Densitymapbox(
    lat=classified_points['Latitude'],
    lon=classified_points['Longitude'],
    radius=30,  # Adjust radius for kernel density estimation
    colorscale=[[0,"green"], [0.5, "yellow"], [1, "red"]],  # Red, green, yellow colors
    zmax=10,
    zmin=2,
    name='Density Heatmap'
))

# Adding vehicle locations (distance < 15 kms) in green with transparency
fig.add_trace(go.Scattermapbox(
    lat=vehicles_near['Latitude'],
    lon=vehicles_near['Longitude'],
    mode='markers',
    marker=dict(color='green', size=15, opacity=0.5),
    name="Vehicles < 15Km"
))

# Adding vehicle locations (distance >= 15 kms) in red with transparency
fig.add_trace(go.Scattermapbox(
    lat=vehicles_far['Latitude'],
    lon=vehicles_far['Longitude'],
    mode='markers',
    marker=dict(color='red', size=15, opacity=0.5),
    name="Vehicles >= 15Km"
))

# Adding workshop locations in blue with transparency
fig.add_trace(go.Scattermapbox(
    lat=df_workshop['Lattitude'],
    lon=df_workshop['Longitude'],
    mode='markers',
    marker=dict(color='blue', size=15, opacity=1),
    name="Workshops"
))

# Update the layout of the plot to use a mapbox style and set the center and zoom level for India
fig.update_layout(
    mapbox_style='open-street-map', 
    mapbox_center_lon=78.9629,  # Approximate center longitude of India
    mapbox_center_lat=20.5937,  # Approximate center latitude of India
    mapbox_zoom=5,  # Zoom level for India
    legend=dict(yanchor="top", y=0.99, xanchor="left", x=0.01)
)

# Save the plot as an HTML file
import plotly.io as pio
pio.write_html(fig, file='map_plot.html', auto_open=True)

# Show the plot
fig.show()


In [34]:
import plotly.graph_objects as go
import pandas as pd
import numpy as np

# Sample data for demonstration (replace this with your actual data)

# Filtering vehicles based on distance from the workshop
vehicles_near = classified_points[classified_points['distance'] < 15]
vehicles_far = classified_points[classified_points['distance'] >= 15]

# Define the figure
fig = go.Figure()

# Adding heatmap trace
fig.add_trace(go.Densitymapbox(
    lat=classified_points['Latitude'],
    lon=classified_points['Longitude'],
    radius=10,  # Smaller radius for more detailed heatmap
    colorscale=[[0, "blue"], [0.5, "orange"], [1, "red"]],  # Red, green, yellow colors
    zmax=1,
    zmin=0,
    opacity=0.6,
    name='Density Heatmap'
))

# Adding vehicle locations (distance < 15 kms) in green with transparency
fig.add_trace(go.Scattermapbox(
    lat=vehicles_near['Latitude'],
    lon=vehicles_near['Longitude'],
    mode='markers',
    marker=dict(color='green', size=15, opacity=0.5),
    text=vehicles_near['vehicleId_count'],
    hoverinfo='text',
    name="Vehicles < 15Km"
))

# Adding vehicle locations (distance >= 15 kms) in red with transparency
fig.add_trace(go.Scattermapbox(
    lat=vehicles_far['Latitude'],
    lon=vehicles_far['Longitude'],
    mode='markers',
    marker=dict(color='maroon', size=15, opacity=0.5),
    text=vehicles_far['vehicleId_count'],
    hoverinfo='text',
    name="Vehicles >= 15Km"
))

# Adding workshop locations in blue with transparency
fig.add_trace(go.Scattermapbox(
    lat=df_workshop['Lattitude'],
    lon=df_workshop['Longitude'],
    mode='markers',
    marker=dict(color='blue', size=15, opacity=0.5),
    name="Workshops"
))

# Update the layout of the plot to use a mapbox style and set the center and zoom level for India
fig.update_layout(
    mapbox_style='open-street-map', 
    mapbox_center_lon=78.9629,  # Approximate center longitude of India
    mapbox_center_lat=20.5937,  # Approximate center latitude of India
    mapbox_zoom=5,  # Zoom level for India
    legend=dict(yanchor="top", y=0.99, xanchor="left", x=0.01)
)

# Save the plot as an HTML file
import plotly.io as pio
pio.write_html(fig, file='map_plot.html', auto_open=True)

# Show the plot
fig.show()


# Latest